In [6]:
!git lfs install

Git LFS initialized.


In [7]:
#!pip install pyttsx3

In [8]:
!git clone https://huggingface.co/sentence-transformers/all-MiniLM-L6-v2

fatal: destination path 'all-MiniLM-L6-v2' already exists and is not an empty directory.


In [9]:
!pip install pyttsx3

In [10]:
import torch
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from transformers import T5ForConditionalGeneration, T5Tokenizer
from transformers import pipeline
from langchain import HuggingFacePipeline
from langchain.prompts import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.vectorstores import FAISS
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import PyMuPDFLoader
from gtts import gTTS
import os
import speech_recognition as sr
import pyttsx3

In [11]:
loader = PyMuPDFLoader(r"D:\f-ai\Pdf vocal query bot\Bcom.Hons Financial&Accounting.pdf")
documents = loader.load()
print(documents)

[Document(page_content='INTERMEDIATE\nSTUDY NOTES\nINTERMEDIATE : PAPER -\n5\nFINANCIAL \nACCOUNTING\nThe Institute of Cost Accountants of India\nCMA Bhawan, 12, Sudder Street, Kolkata - 700 016\n', metadata={'source': 'D:\\f-ai\\Pdf vocal query bot\\Bcom.Hons Financial&Accounting.pdf', 'file_path': 'D:\\f-ai\\Pdf vocal query bot\\Bcom.Hons Financial&Accounting.pdf', 'page': 0, 'total_pages': 1104, 'format': 'PDF 1.6', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'creator': 'Adobe InDesign CS6 (Windows)', 'producer': 'Adobe PDF Library 10.0.1', 'creationDate': "D:20160311140348+05'30'", 'modDate': "D:20160311140348+05'30'", 'trapped': ''}), Document(page_content='First Edition : February 2013\nRevised Edition : May 2013\nSecond Edition : July 2013\nThird Edition : March 2014\nFourth Edition : March 2016\nPublished by :\nDirectorate of Studies\nThe Institute of Cost Accountants of India (ICAI)\nCMA Bhawan, 12, Sudder Street, Kolkata - 700 016\nPrinted at :\nRepro India Limi

In [12]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=150)
docs = text_splitter.split_documents(documents)

In [13]:
docs

[Document(page_content='INTERMEDIATE\nSTUDY NOTES\nINTERMEDIATE : PAPER -\n5\nFINANCIAL \nACCOUNTING\nThe Institute of Cost Accountants of India\nCMA Bhawan, 12, Sudder Street, Kolkata - 700 016', metadata={'source': 'D:\\f-ai\\Pdf vocal query bot\\Bcom.Hons Financial&Accounting.pdf', 'file_path': 'D:\\f-ai\\Pdf vocal query bot\\Bcom.Hons Financial&Accounting.pdf', 'page': 0, 'total_pages': 1104, 'format': 'PDF 1.6', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'creator': 'Adobe InDesign CS6 (Windows)', 'producer': 'Adobe PDF Library 10.0.1', 'creationDate': "D:20160311140348+05'30'", 'modDate': "D:20160311140348+05'30'", 'trapped': ''}),
 Document(page_content='First Edition : February 2013\nRevised Edition : May 2013\nSecond Edition : July 2013\nThird Edition : March 2014\nFourth Edition : March 2016\nPublished by :\nDirectorate of Studies\nThe Institute of Cost Accountants of India (ICAI)\nCMA Bhawan, 12, Sudder Street, Kolkata - 700 016\nPrinted at :\nRepro India Limit

In [14]:
modelPath = "all-MiniLM-L6-v2"
model_kwargs = {'device':'cpu'}
encode_kwargs = {'normalize_embeddings':False}
embeddings = HuggingFaceEmbeddings(
  model_name = modelPath,
  model_kwargs = model_kwargs,
  encode_kwargs=encode_kwargs
)

In [15]:
db = FAISS.from_documents(docs, embeddings)
question = "Define Cost Accounting?"
searchDocs = db.similarity_search(question)
print(searchDocs[0].page_content)

has made profit or loss and the other to know the position of resources that are used by the business.
It can be noted that although accounting is often referred to as an art, it is a science also. This is because 
it is based on universally applicable set of rules. However, it is not a pure science as there is a possibility 
of different interpretation.
(c) Cost Accounting
According to the Chartered Institute of Management Accountants (CIMA), Cost Accountancy is defined 
as “application of costing and cost accounting principles, methods and techniques to the science, 
art and practice of cost control and the ascertainment of profitability as well as the presentation of 
information for the purpose of managerial decision-making.”
It is a branch of accounting dealing with the classification, recording, allocation, summarization and 
reporting of current and prospective costs and analyzing their behaviours. Cost Accounting is frequently


In [16]:
from transformers import pipeline
# Initialize the summarization pipeline
summarizer = pipeline("summarization")

def response_generator(question):
    searchDocs = db.similarity_search(question)
    # Summarize the retrieved content
    summary = summarizer(searchDocs[0].page_content, max_length=150, min_length=50, do_sample=False)
    #print(summary[0]['summary_text'])
    return summary[0]['summary_text']


No model was supplied, defaulted to sshleifer/distilbart-cnn-12-6 and revision a4f8f3e (https://huggingface.co/sshleifer/distilbart-cnn-12-6).
Using a pipeline without specifying a model name and revision in production is not recommended.


In [71]:
response_generator("What is cost accounting")

' Cost Accountancy is a branch of accounting dealing with the classification, recording, allocation, summarization and summarization of current and prospective costs and analyzing their behaviours . Cost Accounting is often referred to as an art, it is a science also .'

In [13]:
from langchain.chains.question_answering import load_qa_chain

def get_conversational_chain():

    prompt_template = """
    Answer the question as detailed as possible from the provided context, make sure to provide all the details, if the answer is not in
    provided context just say, "answer is not available in the context", don't provide the wrong answer\n\n
    Context:\n {context}?\n
    Question: \n{question}\n

    Answer:
    """

    model = llm

    prompt = PromptTemplate(template = prompt_template, input_variables = ["context", "question"])
    chain = load_qa_chain(model, chain_type="stuff", prompt=prompt)

    return chain


In [68]:
def user_input(user_question):
    embeddings = HuggingFaceEmbeddings(
  model_name = modelPath,
  model_kwargs = model_kwargs,
  encode_kwargs=encode_kwargs
)
    
    #new_db = FAISS.load_local("faiss_index", embeddings, allow_dangerous_deserialization=True)
    docs = db.similarity_search(user_question)

    chain = get_conversational_chain()

    
    response = chain(
        {"input_documents":docs, "question": user_question}
        , return_only_outputs=True)

    return response 

In [69]:
user_input("what is cose accounting?")

NameError: name 'get_conversational_chain' is not defined

In [12]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, pipeline
from langchain import HuggingFacePipeline

tokenizer = AutoTokenizer.from_pretrained("flan-t5-large")
tokenizer = AutoTokenizer.from_pretrained("flan-t5-large")
model = AutoModelForSeq2SeqLM.from_pretrained("flan-t5-large")
pipe = pipeline("text2text-generation", model=model, tokenizer=tokenizer, max_new_tokens=100000000)

llm = HuggingFacePipeline(
    pipeline = pipe,
    model_kwargs={"temperature": 0},
)

In [43]:
from langchain.prompts import PromptTemplate

template = """You are a Question-Answering Expert Bot. Your job is to answer the query given by the user as detailed as possible.
{context}
Question: {question}
Helpful Answer:"""
QA_CHAIN_PROMPT = PromptTemplate.from_template(template)

In [44]:
from langchain.chains import RetrievalQA
qa_chain = RetrievalQA.from_chain_type(
  llm=llm,
  chain_type="stuff",
  retriever=db.as_retriever(),
  chain_type_kwargs={"prompt": QA_CHAIN_PROMPT}
)

In [20]:
# Define the TTS functionality
def text_to_speech(text):
    tts = gTTS(text=text, lang='en')
    tts.save("output.mp3")
    os.system("mpg321 output.mp3")

In [21]:
recognizer = sr.Recognizer()

In [47]:
# Define Q&A bot
class QABot:
    def __init__(self):
        self.qa_chain = qa_chain

    def answer(self, query):
        result = self.qa_chain({"query": query})
        return result["result"]

    def speak(self, query):
        text = self.answer(query)
        text_to_speech(text)
        return text


In [48]:
# Create the Q&A bot instance
bot = QABot()

In [48]:
listening = True
stop_input = 'f'
# Define speech recognition function
def speech_recognition():
    global listening
    r = sr.Recognizer()
    with sr.Microphone() as source:
        while listening == True:    
            print("Say something!")
        
            stop_input = input("Press e to stop listening : ")
            audio = r.listen(source)
            try:
                text = r.recognize_google(audio, language="en-GB")
                
                return text
            except sr.UnknownValueError:
                print("Google Speech Recognition could not understand your audio")
            except sr.RequestError as e:
                print(f"Could not request results from Google Speech Recognition service; {e}")

In [76]:
import speech_recognition as sr

def speech_recognition():

    # obtain audio from the microphone
    r = sr.Recognizer()

    # Flag to control listening loop
    listening = True

    with sr.Microphone() as source:
        print("Say something!")
        while listening:
            audio = r.listen(source,phrase_time_limit=5,timeout=6)
            
            # Check if stop command is detected
            try:
                command = r.recognize_google(audio)
                print("You said: " + command)
                return command
                
                # Check if the command is the stop keyword
                if "stop listening" in command.lower():
                    print("Stop command detected. Stopping listening.")
                    return command
                    listening = False  # Set listening flag to False to stop the loop
            except sr.UnknownValueError:
                print("Google Speech Recognition could not understand audio")
            except sr.RequestError as e:
                print("Could not request results from Google Speech Recognition service; {0}".format(e))


In [44]:
def convert_voice_to_text(audio):
     try:
         text = recognizer.recognize_google(audio)
         print("You said: " + text)
     except sr.UnknownValueError:
         text = ""
         print("Sorry, I didn't understand that.")
     except sr.RequestError as e:
         text = ""
         print("Error; {0}".format(e))
     return text

In [51]:
# bot = pyttsx3.init()

In [52]:
# def main():
#     end_program = False
#     while not end_program:
#         print("1. Speak your query.")
#         print("2. Type your query.")
#         choice = input("Enter your choice (1/2): ")

#         if choice == "1":
#             r = sr.Recognizer()
#             with sr.Microphone() as source:
#                 print("Speak your query...")
#                 audio = r.listen(source)
#             try:
#                 query = r.recognize_google(audio, language="en-US")
#                 response = bot.speak(query)
#                 print("Response:", response)
#             except sr.UnknownValueError:
#                 print("Google Speech Recognition could not understand your query")
#             except sr.RequestError as e:
#                 print("Could not request results from Google Speech Recognition service; {0}".format(e))
#         elif choice == "2":
#             query = input("Enter your query: ")
#             response = bot.answer(query)
#             print("Response:", response)
#         else:
#             print("Invalid choice!")
#         cont = input("Do you want to continue? (yes/no): ")
#         if cont.lower() != "yes":
#             end_program = True

In [77]:
# Define the main functionality
def main():
    while True:
        print("1. Speak your query.")
        print("2. Type your query.")
        choice = input("Enter your choice (1/2): ")

        if choice == "1":
            query = speech_recognition()
            response = response_generator(query)
            print("Query : " ,query , "Response:", response)
            text_to_speech(response)
        elif choice == "2":
            query = input("Enter your query: ")
            response = response_generator(query)
            print("Response:", response)
        else:
            print("Invalid choice!")

In [55]:
!pip install pyaudio

   ---------------------------------------- 0.0/164.1 kB ? eta -:--:--
   --------- ----------------------------- 41.0/164.1 kB 991.0 kB/s eta 0:00:01
   ---------------------------------------  163.8/164.1 kB 2.5 MB/s eta 0:00:01
   ---------------------------------------- 164.1/164.1 kB 1.6 MB/s eta 0:00:00


In [79]:
if __name__ == "__main__":
    main()

1. Speak your query.
2. Type your query.
Say something!
You said: what is cost accounting
Query :  what is cost accounting Response:  Cost Accountancy is a branch of accounting dealing with the classification, recording, allocation, summarization and summarization of current and prospective costs and analyzing their behaviours . Cost Accounting is often referred to as an art, it is a science also .
1. Speak your query.
2. Type your query.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening

KeyboardInterrupt: Interrupted by user

Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop command detected. Stopping listening.
Stop comman

In [ ]:
# Define the Q&A bot
class QABot:
    def __init__(self):
        self.qa_chain = qa_chain

    def answer(self, query):
        result = self.qa_chain({"query": query})
        return result["result"]

    def speak(self, query):
        text = self.answer(query)
        text_to_speech(text)

In [ ]:
def get_answer(self, query):
    result = self.qa_chain({"query": query})
    return result["result"]

In [ ]:
def speak(self, query):
        text = self.get_answer(query)
        text_to_speech(text)
        print(text)

In [ ]:
# Create the Q&A bot
bot = QABot()

In [ ]:
# Define the speech recognition functionality
def speech_recognition():
    r = sr.Recognizer()
    with sr.Microphone() as source:
        print("Say something!")
        audio = r.listen(source)
        try:
            text = r.recognize_google(audio, language="en-GB")
            return text
        except sr.UnknownValueError:
            print("Google Speech Recognition could not understand your audio")
        except sr.RequestError as e:
            print(f"Could not request results from Google Speech Recognition service; {e}")

In [ ]:
# Define the main functionality
def main():
    while True:
        query = speech_recognition()
        bot.speak(query)

In [ ]:
if __name__ == "__main__":
    main()

AttributeError: Could not find PyAudio; check installation

In [ ]:
# Test the Q&A bot
bot.speak("Define Equity Share?")

ValueError: The following `model_kwargs` are not used by the model: ['return_full_text'] (note: typos in the generate arguments will also show up in this list)